In [14]:
import osmnx as ox
import networkx as nx
from shapely.geometry import Point
import sys

sys.path.append("../src/")

from utils import (
    get_route,
    get_nearest_station,
    get_valencian_open_data,
    get_valenbisi_stations)

In [2]:
def get_route(start, end, graph):
    """
    Get the route between two nodes in the graph.

    Parameters:
        start(tuple): Tuple of coordenates for the start point.
        end: Tuple of coordinates for the end point.
        graph: The cycling network graph.

    Returns:
        list: A list of nodes representing the route.
    """
    from_node = ox.distance.nearest_nodes(graph, start[1], start[0])
    to_node = ox.distance.nearest_nodes(graph, end[1], end[0])

    route = ox.shortest_path(graph, from_node, to_node, weight="length")
    return route

In [3]:
graph = ox.load_graphml("../data/valencia_walking_network.graphml")

In [4]:
for ini, fin, info in graph.edges(data=True):
    print(info)
    break

{'osmid': 803049226, 'highway': 'footway', 'oneway': False, 'reversed': False, 'length': 8.794706111104842}


In [5]:
inicio = (39.478316, -0.373266)
fin = (39.467615, -0.377149)

route = get_route(inicio, fin, graph)

In [6]:

def get_nearest_station(point, gdf):
    """
    Devuelve la estación más cercana (como fila del GeoDataFrame) al punto dado,
    usando distancia euclídea en metros con reproyección a EPSG:25830.

    Parámetros:
        point (tuple): (lat, lon) en EPSG:4326
        gdf (GeoDataFrame): con geometría en EPSG:4326

    Retorna:
        GeoSeries: fila de la estación más cercana con columna 'distance' en metros
    """
    # Reproyectar a sistema métrico (UTM zona 30N para Valencia)
    gdf_proj = gdf.to_crs(epsg=25830)

    # Crear punto y reproyectar
    point_geom = gpd.GeoSeries([Point(point[1], point[0])], crs="EPSG:4326").to_crs(epsg=25830).iloc[0]

    # Calcular distancias
    gdf_proj["distance"] = gdf_proj.distance(point_geom)

    # Obtener estación más cercana
    nearest_row = gdf_proj.loc[gdf_proj["distance"].idxmin()]

    return nearest_row
    

In [7]:
import geopandas as gpd

# Cargar el GeoJSON
valenbisi_gdf = gpd.read_file("../data/valenbisi_stations.geojson")

# Asegurar que está en CRS WGS84 (lat/lon)
if valenbisi_gdf.crs is None or valenbisi_gdf.crs.to_epsg() != 4326:
    valenbisi_gdf = valenbisi_gdf.to_crs(epsg=4326)

# Comprobar contenido
print(valenbisi_gdf.head())
print("CRS:", valenbisi_gdf.crs)


                                         address  number open  available  \
0            Antonio Ferrandis - General Urrutia      48    T         11   
1                   Vicent Vidal - Pintor Maella      61    T          4   
2  Blasco Ibañez - Doctor Gómez Ferrer (Clínico)      87    T         23   
3                 Gaspar Aguilar - Vicente Parra      86    T          2   
4                  Escultor José Capuz - Oriente      43    T          7   

   free  total ticket           updated_at  \
0     9     20      F  12/06/2025 12:03:30   
1    14     20      F  12/06/2025 12:03:30   
2     9     33      F  12/06/2025 12:03:30   
3    18     20      F  12/06/2025 12:03:30   
4    13     20      F  12/06/2025 12:03:30   

                                           geo_shape  \
0  { "type": "Feature", "geometry": { "coordinate...   
1  { "type": "Feature", "geometry": { "coordinate...   
2  { "type": "Feature", "geometry": { "coordinate...   
3  { "type": "Feature", "geometry": { "coo

In [8]:


def get_nearest_station(point, gdf):
    gdf_proj = gdf.to_crs(epsg=25830)
    point_geom = gpd.GeoSeries([Point(point[1], point[0])], crs="EPSG:4326").to_crs(epsg=25830).iloc[0]
    gdf_proj["distance"] = gdf_proj.distance(point_geom)
    nearest_row = gdf_proj.loc[gdf_proj["distance"].idxmin()]
    return nearest_row


In [15]:
punto = (39.4700, -0.3760)  # (lat, lon)
nearest = get_nearest_station(punto, valenbisi_gdf)


In [17]:
print(" Estación más cercana:", nearest["address"])
print(" Distancia:", round(nearest["distance"], 1), "m")
print(" Bicis disponibles:", nearest["available"])
print(" Coordenadas:", nearest.geometry.y, nearest.geometry.x)


 Estación más cercana: Ribera - Plaza Ayuntamiento
 Distancia: 105.9 m
 Bicis disponibles: 12
 Coordenadas: 4372121.701497201 725755.3392026019


In [18]:
nearest

address                               Ribera - Plaza Ayuntamiento
number                                                         15
open                                                            T
available                                                      12
free                                                           22
total                                                          34
ticket                                                          F
updated_at                                    12/06/2025 12:03:30
geo_shape       { "type": "Feature", "geometry": { "coordinate...
geo_point_2d    { "lon": -0.37563738804340713, "lat": 39.46908...
update_jcd                              2025-06-12 11:53:12+00:00
nearest_node                                           7575421293
geometry              POINT (725755.3392026019 4372121.701497201)
distance                                               105.943773
Name: 10, dtype: object

In [25]:
import pandas as pd

arboles = pd.read_csv("../data/arbratge-arbolado.csv", sep=';')


In [26]:
arboles.columns

Index(['OBJECTID', 'Unidad de Gestion', 'Tipo Situacion', 'Barrio', 'Lugar',
       'Id. Arbol', 'Nombre Botánico', 'Nombre Comun Castellano',
       'Nombre Comun Valenciano', 'Grupo', 'LPAMCV', 'DISTRITO', 'geo_shape',
       'geo_point_2d'],
      dtype='object')

In [27]:
arboles

OBJECTID Unidad de Gestion Tipo Situacion                    Barrio  \
0        3876777              VSJS         Viario  104 - LA FONTETA S.LLUIS   
1        3876779              VSJS         Viario       134 - LA VEGA BAIXA   
2        3876785              VSJS         Viario      131 - L'ILLA PERDUDA   
3        3876786              VSJS         Viario           133 - L'AMISTAT   
4        3876801              VSJS         Viario        142 - CAMI DE VERA   
...          ...               ...            ...                       ...   
159163   3919141              VSJS         Viario              81 - PATRAIX   
159164   3920647              VSJS         Viario    123 - LA CREU DEL GRAU   
159165   3923927              VSJS         Viario               121 - AIORA   
159166   3924542              VSJS         Viario               121 - AIORA   
159167   3924602              VSJS         Viario               121 - AIORA   

                           Lugar   Id. Arbol                  Nombre Botánico  \
0                    MÚSIC CHAPÍ     51600/2              Cercis siliquastrum   
1                         SERPIS    70920/29  Ligustrum japonicum 'Variegata'   
2         POETA ANDRÉS CABRELLES    60030/49  Ligustrum japonicum 'Variegata'   
3                BEATRIZ TORTOSA     9480/26  Ligustrum japonicum 'Variegata'   
4                      TARONGERS  42340/1166        Phoenix dactylifera macho   
...                          ...         ...                              ...   
159163                      XIVA     22740/4                 Citrus aurantium   
159164  HIGINIO NOJA (PROFESSOR)   67230/139                 Citrus aurantium   
159165          RAMIRO DE MAEZTU    62640/30                 Citrus aurantium   
159166          RAMIRO DE MAEZTU    62640/29                 Citrus aurantium   
159167          RAMIRO DE MAEZTU    62640/26                 Citrus aurantium   

       Nombre Comun Castellano  Nombre Comun Valenciano     Grupo LPAMCV  \
0               Árbol del amor         Arbre de l' amor    Caduco     SD   
1          Aligustre variegado       Aligustre variegat   Perenne     SD   
2          Aligustre variegado       Aligustre variegat   Perenne     SD   
3          Aligustre variegado       Aligustre variegat   Perenne     SD   
4       Palmera datilera macho  Palmera datilera mascle  Palmacea     SD   
...                        ...                      ...       ...    ...   
159163          Naranjo amargo            Taronger bord   Perenne     SD   
159164          Naranjo amargo            Taronger bord   Perenne    NaN   
159165          Naranjo amargo            Taronger bord   Perenne     SD   
159166          Naranjo amargo            Taronger bord   Perenne     SD   
159167          Naranjo amargo            Taronger bord   Perenne     SD   

                    DISTRITO  \
0       10 - QUATRE CARRERES   
1               13 - ALGIROS   
2               13 - ALGIROS   
3               13 - ALGIROS   
4            14 - BENIMACLET   
...                      ...   
159163           8 - PATRAIX   
159164   12 - CAMINS AL GRAU   
159165   12 - CAMINS AL GRAU   
159166   12 - CAMINS AL GRAU   
159167   12 - CAMINS AL GRAU   

                                                geo_shape  \
0       {"coordinates": [-0.3651314386419635, 39.44621...   
1       {"coordinates": [-0.3474188781861639, 39.47583...   
2       {"coordinates": [-0.3420191605279348, 39.46919...   
3       {"coordinates": [-0.34878607890854607, 39.4727...   
4       {"coordinates": [-0.35587184033892966, 39.4922...   
...                                                   ...   
159163  {"coordinates": [-0.3916080164861607, 39.46606...   
159164  {"coordinates": [-0.3458420186899667, 39.46269...   
159165  {"coordinates": [-0.34537296767244324, 39.4666...   
159166  {"coordinates": [-0.3454494105293515, 39.46663...   
159167  {"coordinates": [-0.34565795158697865, 39.4667...   

                                    geo_point_2d  
0   

In [28]:

# Separar lat y lon directamente desde las tuplas
arboles["lat"] = arboles["geo_point_2d"].apply(lambda x: eval(x)[0])
arboles["lon"] = arboles["geo_point_2d"].apply(lambda x: eval(x)[1])

# Crear GeoDataFrame
gdf_arboles = gpd.GeoDataFrame(
    arboles,
    geometry=gpd.points_from_xy(arboles["lon"], arboles["lat"]),
    crs="EPSG:4326"
)

In [29]:
import folium

m = folium.Map(location=[39.47, -0.376], zoom_start=14)

for _, row in gdf_arboles.iterrows():
    folium.CircleMarker(
        location=(row["lat"], row["lon"]),
        radius=2,
        color="green",
        fill=True,
        fill_opacity=0.6,
        popup=row.get("Nombre Comun Castellano", "")
    ).add_to(m)

m

KeyboardInterrupt: 

In [35]:
from folium.plugins import MarkerCluster

m = folium.Map(location=[39.47, -0.376], zoom_start=14)
marker_cluster = MarkerCluster().add_to(m)

for _, row in gdf_filtrado.iterrows():
    folium.CircleMarker(
        location=(row["lat"], row["lon"]),
        radius=2,
        color="green",
        fill=True,
        fill_opacity=0.6,
        popup=row.get("Nombre Comun Castellano", "")
    ).add_to(marker_cluster)

m


In [34]:
gdf_filtrado = gdf_arboles.head(4000)


In [33]:
gdf_arboles

OBJECTID Unidad de Gestion Tipo Situacion                    Barrio  \
0        3876777              VSJS         Viario  104 - LA FONTETA S.LLUIS   
1        3876779              VSJS         Viario       134 - LA VEGA BAIXA   
2        3876785              VSJS         Viario      131 - L'ILLA PERDUDA   
3        3876786              VSJS         Viario           133 - L'AMISTAT   
4        3876801              VSJS         Viario        142 - CAMI DE VERA   
...          ...               ...            ...                       ...   
159163   3919141              VSJS         Viario              81 - PATRAIX   
159164   3920647              VSJS         Viario    123 - LA CREU DEL GRAU   
159165   3923927              VSJS         Viario               121 - AIORA   
159166   3924542              VSJS         Viario               121 - AIORA   
159167   3924602              VSJS         Viario               121 - AIORA   

                           Lugar   Id. Arbol                  Nombre Botánico  \
0                    MÚSIC CHAPÍ     51600/2              Cercis siliquastrum   
1                         SERPIS    70920/29  Ligustrum japonicum 'Variegata'   
2         POETA ANDRÉS CABRELLES    60030/49  Ligustrum japonicum 'Variegata'   
3                BEATRIZ TORTOSA     9480/26  Ligustrum japonicum 'Variegata'   
4                      TARONGERS  42340/1166        Phoenix dactylifera macho   
...                          ...         ...                              ...   
159163                      XIVA     22740/4                 Citrus aurantium   
159164  HIGINIO NOJA (PROFESSOR)   67230/139                 Citrus aurantium   
159165          RAMIRO DE MAEZTU    62640/30                 Citrus aurantium   
159166          RAMIRO DE MAEZTU    62640/29                 Citrus aurantium   
159167          RAMIRO DE MAEZTU    62640/26                 Citrus aurantium   

       Nombre Comun Castellano  Nombre Comun Valenciano     Grupo LPAMCV  \
0               Árbol del amor         Arbre de l' amor    Caduco     SD   
1          Aligustre variegado       Aligustre variegat   Perenne     SD   
2          Aligustre variegado       Aligustre variegat   Perenne     SD   
3          Aligustre variegado       Aligustre variegat   Perenne     SD   
4       Palmera datilera macho  Palmera datilera mascle  Palmacea     SD   
...                        ...                      ...       ...    ...   
159163          Naranjo amargo            Taronger bord   Perenne     SD   
159164          Naranjo amargo            Taronger bord   Perenne    NaN   
159165          Naranjo amargo            Taronger bord   Perenne     SD   
159166          Naranjo amargo            Taronger bord   Perenne     SD   
159167          Naranjo amargo            Taronger bord   Perenne     SD   

                    DISTRITO  \
0       10 - QUATRE CARRERES   
1               13 - ALGIROS   
2               13 - ALGIROS   
3               13 - ALGIROS   
4            14 - BENIMACLET   
...                      ...   
159163           8 - PATRAIX   
159164   12 - CAMINS AL GRAU   
159165   12 - CAMINS AL GRAU   
159166   12 - CAMINS AL GRAU   
159167   12 - CAMINS AL GRAU   

                                                geo_shape  \
0       {"coordinates": [-0.3651314386419635, 39.44621...   
1       {"coordinates": [-0.3474188781861639, 39.47583...   
2       {"coordinates": [-0.3420191605279348, 39.46919...   
3       {"coordinates": [-0.34878607890854607, 39.4727...   
4       {"coordinates": [-0.35587184033892966, 39.4922...   
...                                                   ...   
159163  {"coordinates": [-0.3916080164861607, 39.46606...   
159164  {"coordinates": [-0.3458420186899667, 39.46269...   
159165  {"coordinates": [-0.34537296767244324, 39.4666...   
159166  {"coordinates": [-0.3454494105293515, 39.46663...   
159167  {"coordinates": [-0.34565795158697865, 39.4667...   

                                    geo_point_2d       

In [ ]:
from shapely.geometry import LineString

def contar_arboles_cerca_ruta(route_coords, gdf_arboles, buffer_metros=20):
    """
    Cuenta cuántos árboles hay a menos de X metros de una ruta.

    Parámetros:
        route_coords (list): Lista de (lat, lon) de la ruta.
        gdf_arboles (GeoDataFrame): GeoDataFrame con geometría de árboles.
        buffer_metros (int): Distancia desde la ruta para contar árboles.

    Retorna:
        int: número de árboles cerca de la ruta
    """
    route_line = LineString([(lon, lat) for lat, lon in route_coords])  # shapely usa lon,lat
    route_gdf = gpd.GeoDataFrame(geometry=[route_line], crs="EPSG:4326")
    route_gdf = route_gdf.to_crs(epsg=25830)
    route_buffer = route_gdf.buffer(buffer_metros).to_crs(epsg=4326).iloc[0]
    return gdf_arboles[gdf_arboles.geometry.within(route_buffer)].shape[0]


In [37]:
# Ver los atributos de una arista cualquiera
edge_data = list(graph.edges(data=True))[0]
print("Ejemplo de arista (edge):", edge_data)

# Ver atributos de un nodo cualquiera
node_data = list(graph.nodes(data=True))[0]
print("Ejemplo de nodo:", node_data)

# Ver CRS si está disponible
print("CRS del grafo:", graph.graph.get("crs", "desconocido"))


Ejemplo de arista (edge): (25767290, 11420770018, {'osmid': 803049226, 'highway': 'footway', 'oneway': False, 'reversed': False, 'length': 8.794706111104842})
Ejemplo de nodo: (25767290, {'y': 39.4703478, 'x': -0.3759153, 'highway': 'crossing', 'street_count': 4})
CRS del grafo: epsg:4326


In [38]:
print(gdf_arboles.head())
print("\nColumnas disponibles:", gdf_arboles.columns)
print("\nCRS del GeoDataFrame:", gdf_arboles.crs)
print("\nTipo de geometría:", gdf_arboles.geometry.iloc[0])


   OBJECTID Unidad de Gestion Tipo Situacion                    Barrio  \
0   3876777              VSJS         Viario  104 - LA FONTETA S.LLUIS   
1   3876779              VSJS         Viario       134 - LA VEGA BAIXA   
2   3876785              VSJS         Viario      131 - L'ILLA PERDUDA   
3   3876786              VSJS         Viario           133 - L'AMISTAT   
4   3876801              VSJS         Viario        142 - CAMI DE VERA   

                    Lugar   Id. Arbol                  Nombre Botánico  \
0             MÚSIC CHAPÍ     51600/2              Cercis siliquastrum   
1                  SERPIS    70920/29  Ligustrum japonicum 'Variegata'   
2  POETA ANDRÉS CABRELLES    60030/49  Ligustrum japonicum 'Variegata'   
3         BEATRIZ TORTOSA     9480/26  Ligustrum japonicum 'Variegata'   
4               TARONGERS  42340/1166        Phoenix dactylifera macho   

  Nombre Comun Castellano  Nombre Comun Valenciano     Grupo LPAMCV  \
0          Árbol del amor         Arbre

In [45]:
import osmnx as ox 
import geopandas as gpd
import numpy as np
from tqdm import tqdm

# Cargar grafo
edges = ox.graph_to_gdfs(graph, nodes=False)

# Asegurar que arboles sea un GeoDataFrame y tenga el mismo CRS
arboles = gpd.GeoDataFrame(arboles, geometry="geometry", crs=edges.crs)

# Índice espacial para árboles
sindex = arboles.sindex

# Definir tramos de temperatura y sus pesos (longitud, sombra)
tramos = [(0, 5), (5, 10), (10, 15), (15, 20), (20, 25), (25, 30), (30, 35), (35, 40)]
pesos = {
    (0, 5): (0.7, 0.3),
    (5, 10): (0.6, 0.4),
    (10, 15): (0.5, 0.5),
    (15, 20): (0.4, 0.6),
    (20, 25): (0.3, 0.7),
    (25, 30): (0.2, 0.8),
    (30, 35): (0.1, 0.9),
    (35, 40): (0.05, 0.95),
}

# Radio de búsqueda para árboles (en metros, aproximadamente)
radio = 15

# Función para contar árboles cercanos usando sindex
def contar_arboles_cercanos(geom):
    posibles = list(sindex.intersection(geom.buffer(radio).bounds))
    cercanos = arboles.iloc[posibles]
    return cercanos.distance(geom).lt(radio).sum()

# Calcular número de árboles cercanos por arista con barra de progreso
edges["num_arboles"] = [
    contar_arboles_cercanos(geom) for geom in tqdm(edges.geometry, desc="Calculando sombra")
]

# Calcular pesos por temperatura
for tramo in tramos:
    t_str = f"peso_{tramo[0]}_{tramo[1]}"
    w_len, w_sombra = pesos[tramo]
    edges[t_str] = w_len * edges["length"] - w_sombra * edges["num_arboles"]

# Mostrar resultados
print(edges[[col for col in edges.columns if "peso_" in col]].head())


Calculando sombra:   0%|          | 0/126948 [00:00<?, ?it/s]C:\Users\carle\AppData\Local\Temp\ipykernel_17336\4203973022.py:35: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  return cercanos.distance(geom).lt(radio).sum()
Calculando sombra:   0%|          | 617/126948 [03:15<11:06:56,  3.16it/s]


KeyboardInterrupt: 

In [46]:
import osmnx as ox 
import geopandas as gpd
import numpy as np
from tqdm import tqdm

# Cargar grafo
edges = ox.graph_to_gdfs(graph, nodes=False)

# Filtrar las primeras 100 aristas para prueba
edges_sample = edges.head(100).copy()

# Asegurar que arboles sea un GeoDataFrame con CRS igual
arboles = gpd.GeoDataFrame(arboles, geometry="geometry", crs=edges.crs)

# Índice espacial de árboles
sindex = arboles.sindex

# Tramo de temperatura a procesar
tramo = (25, 30)
peso_key = f"peso_{tramo[0]}_{tramo[1]}"
w_len, w_sombra = 0.2, 0.8  # pesos definidos para ese tramo

# Radio de búsqueda (metros)
radio = 15

# Función para contar árboles cercanos a una arista
def contar_arboles_cercanos(geom):
    posibles = list(sindex.intersection(geom.buffer(radio).bounds))
    cercanos = arboles.iloc[posibles]
    return cercanos.distance(geom).lt(radio).sum()

# Calcular árboles cercanos con barra de progreso
edges_sample["num_arboles"] = [
    contar_arboles_cercanos(geom) for geom in tqdm(edges_sample.geometry, desc="Calculando sombra (test)")
]

# Calcular el peso solo para ese tramo
edges_sample[peso_key] = w_len * edges_sample["length"] - w_sombra * edges_sample["num_arboles"]

# Ver resultado
print(edges_sample[[peso_key, "length", "num_arboles"]].head())


Calculando sombra (test):   0%|          | 0/100 [00:00<?, ?it/s]C:\Users\carle\AppData\Local\Temp\ipykernel_17336\3376422833.py:30: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  return cercanos.distance(geom).lt(radio).sum()
Calculando sombra (test): 100%|██████████| 100/100 [00:25<00:00,  3.98it/s]

                             peso_25_30     length  num_arboles
u        v           key                                       
25767290 11420770018 0   -127332.641059   8.794706       159168
         11420770019 0   -127333.545012   4.274938       159168
         11420770020 0   -127333.610666   3.946669       159168
         524790982   0   -127331.648920  13.755401       159168
25767292 6766690060  0   -127323.069464  56.652682       159168


In [47]:
import osmnx as ox
import geopandas as gpd
import numpy as np
from shapely.geometry import Point
from tqdm import tqdm

# Proyectamos a sistema métrico (EPSG:25830 es válido para Valencia)
graph_proj = ox.project_graph(graph, to_crs="EPSG:25830")
edges = ox.graph_to_gdfs(graph_proj, nodes=False)

# Proyectar árboles
arboles_proj = arboles.copy()
arboles_proj = gpd.GeoDataFrame(arboles_proj, geometry="geometry", crs="EPSG:4326")
arboles_proj = arboles_proj.to_crs(edges.crs)

# Crear índice espacial para eficiencia
sindex = arboles_proj.sindex

# Parámetros
radio = 15  # metros
w_len, w_sombra = 0.2, 0.8  # pesos para temperatura 25-30 °C

# Calcular número de árboles cercanos
def contar_arboles_cercanos(geom):
    posibles = list(sindex.intersection(geom.buffer(radio).bounds))
    cercanos = arboles_proj.iloc[posibles]
    return cercanos.distance(geom).lt(radio).sum()

# Si quieres probarlo solo con unas pocas aristas:
edges_subset = edges.sample(10, random_state=42).copy()  # Cambia a edges para todo

tqdm.pandas(desc="Calculando sombra")
edges_subset["num_arboles"] = edges_subset.geometry.progress_apply(contar_arboles_cercanos)

# Calcular peso
edges_subset["peso_25_30"] = w_len * edges_subset["length"] - w_sombra * edges_subset["num_arboles"]

# Mostrar resultado
print(edges_subset[["length", "num_arboles", "peso_25_30"]])


Calculando sombra: 100%|██████████| 10/10 [00:00<00:00, 657.53it/s]

                                length  num_arboles  peso_25_30
u           v           key                                    
3536480963  10101947238 0    14.885372            0    2.977074
10873732466 10873732476 0    48.955626            0    9.791125
10248794380 10248794360 0    32.265947            1    5.653189
1636824903  10942249303 1    45.011365            0    9.002273
10908411199 10911332037 0    10.547231            4   -1.090554
11013591667 11013591668 0     9.019294            3   -0.596141
112137514   112137583   0    19.150238            6   -0.969952
11177553400 11177553402 0     5.107707            0    1.021541
4102819109  4102819107  0    54.512278            0   10.902456
11536783077 7195974007  0    25.836072           13   -5.232786


In [52]:
import osmnx as ox

# Obtener GeoDataFrame de aristas
edges = ox.graph_to_gdfs(graph, nodes=False)

# Ver las primeras filas
print(edges.head())

# Ver todas las columnas disponibles
print(edges.columns)


                              osmid      highway  oneway reversed     length  \
u        v           key                                                       
25767290 11420770018 0    803049226      footway   False    False   8.794706   
         11420770019 0    803049226      footway   False     True   4.274938   
         11420770020 0    803466250  residential   False    False   3.946669   
         524790982   0    803466250  residential   False     True  13.755401   
25767292 6766690060  0      5098789   pedestrian   False    False  56.652682   

                         lanes maxspeed                        name  \
u        v           key                                              
25767290 11420770018 0     NaN      NaN                         NaN   
         11420770019 0     NaN      NaN                         NaN   
         11420770020 0       3       30       Plaça de l'Ajuntament   
         524790982   0       3       30       Plaça de l'Ajuntament   
25767292 6766

In [ ]:
from shapely.geometry import LineString

# Supone que G tiene atributo 'geometry' en cada arista y que `arboles` es un GeoDataFrame con CRS correcto
radio = 15
tramos = [(0, 5), (5, 10), (10, 15), (15, 20), (20, 25), (25, 30), (30, 35), (35, 40)]
pesos = {
    (0, 5): (0.7, 0.3),
    (5, 10): (0.6, 0.4),
    (10, 15): (0.5, 0.5),
    (15, 20): (0.4, 0.6),
    (20, 25): (0.3, 0.7),
    (25, 30): (0.2, 0.8),
    (30, 35): (0.1, 0.9),
    (35, 40): (0.05, 0.95),
}

# Crear spatial index para árboles
sindex = arboles.sindex

# Calcular y asignar pesos en cada arista del grafo
for u, v, data in tqdm(graph.edges(data=True)):
    geom = data.get("geometry", None)
    if geom is None:
        #construir un line string del nodo u al nodo v
        u_geom=(
            graph.nodes[u]["y"], graph.nodes[u]["x"]
        )
        v_geom=(
            graph.nodes[v]["y"], graph.nodes[v]["x"]
        )
        geom = LineString([u_geom, v_geom])




        

    # Contar árboles cercanos
    posibles = list(sindex.intersection(geom.buffer(radio).bounds))
    cercanos = arboles.iloc[posibles]
    num_arboles = cercanos.distance(geom).lt(radio).sum()

    data["num_arboles"] = num_arboles
    length = data.get("length", 1)

    # Calcular un peso por cada tramo de temperatura
    for tramo in tramos:
        w_len, w_sombra = pesos[tramo]
        t_str = f"peso_{tramo[0]}_{tramo[1]}"
        data[t_str] = w_len * length - w_sombra * num_arboles+1000


  0%|          | 0/126948 [00:00<?, ?it/s]C:\Users\carle\AppData\Local\Temp\ipykernel_17336\2280196184.py:41: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  num_arboles = cercanos.distance(geom).lt(radio).sum()
  2%|▏         | 2999/126948 [14:40<6:07:17,  5.62it/s] 

In [ ]:
ox.save_graphml(graph, "../data/valencia_walking_sombra.graphml")